In [60]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.impute import SimpleImputer
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder, StandardScaler, LabelEncoder
from sklearn.compose import make_column_transformer
from sklearn.multiclass import OneVsOneClassifier, OneVsRestClassifier
from lightgbm.sklearn import LGBMClassifier
from xgboost import XGBClassifier
from sklearn.model_selection import RandomizedSearchCV, GridSearchCV
from sklearn.ensemble import RandomForestClassifier, VotingClassifier, StackingClassifier

from sklearn.metrics import roc_auc_score, roc_curve
from sklearn.metrics import log_loss
from sklearn.model_selection import StratifiedKFold

from sklearn.feature_selection import RFE

In [61]:
DIR = "../../data/"
SMOOTHIE = "Smoothie King/"

smoothie_demographic = pd.read_csv(DIR + SMOOTHIE + "processed_demographic.csv")
smoothie_stores = pd.read_csv(DIR + SMOOTHIE + "smoothie_king_stores.csv")
smoothie_poi_variables = pd.read_csv(DIR + SMOOTHIE + "processed_poi.csv")
# smoothie_sister = pd.read_csv(DIR + SMOOTHIE + "competition_sister_variables.csv")
smoothie_trade_area = pd.read_csv(DIR + SMOOTHIE + "processed_trade_area.csv").rename(columns={"store_num": "store"})

In [62]:
smoothie_merged = smoothie_stores.merge(
    smoothie_demographic, on="store", how="outer"
).merge(
    smoothie_poi_variables, on="store", how="outer"
).merge(
    smoothie_trade_area, on="store", how="outer"
)
smoothie_merged

store   longitude   latitude  category  \
0    SK 1504  -97.650392  30.519353  SHOPPING   
1    SK 0057  -88.171150  30.672501  SHOPPING   
2    SK 1415  -90.535722  38.784250      HOME   
3    SK 1231  -80.134700  26.100737    TRAVEL   
4    SK 1535  -96.856651  32.996408      WORK   
..       ...         ...        ...       ...   
791  SK 1536  -96.872596  32.647809      HOME   
792  SK 1886 -105.077634  40.564695     OTHER   
793  SK 0162  -95.478001  30.316531  SHOPPING   
794  SK 1449  -78.968258  35.064994  SHOPPING   
795  SK 1351  -98.605570  29.616600      HOME   

                           cbsa_name                  dma_name  \
0              Austin-Round Rock, TX                Austin, TX   
1                         Mobile, AL       Mobile et al, AL-FL   
2                   St. Louis, MO-IL             St. Louis, MO   
3    Miami-Fort Lauderdale et al, FL  Miami-Ft. Lauderdale, FL   
4    Dallas-Fort Worth-Arlington, TX      Dallas-Ft. Worth, TX   
..                               ...                       ...   
791  Dallas-Fort Worth-Arlington, TX      Dallas-Ft. Worth, TX   
792                 Fort Collins, CO                Denver, CO   
793  Houston-The Woodlands et al, TX               Houston, TX   
794                 Fayetteville, NC         Raleigh et al, NC   
795    San Antonio-New Braunfels, TX           San Antonio, TX   

         state_name           market_size   store_density  age0018_p_10mi  \
0             Texas       Large Metro (2)  Light Suburban          0.2805   
1           Alabama       Medium City (4)  Light Suburban          0.2264   
2          Missouri  Very Large Metro (1)  Light Suburban          0.2129   
3           Florida  Very Large Metro (1)        Suburban          0.2174   
4             Texas  Very Large Metro (1)  Light Suburban          0.2620   
..              ...                   ...             ...             ...   
791           Texas  Very Large Metro (1)         Exurban          0.2664   
792        Colorado       Medium City (4)  Light Suburban          0.2224   
793           Texas  Very Large Metro (1)         Exurban          0.2412   
794  North Carolina       Medium City (4)         Exurban          0.2614   
795           Texas  Very Large Metro (1)         Exurban          0.2538   

     ...  popgrfy_ta  popgrpy_ta  poverty_inpoverty_p_ta  \
0    ...      8.3789      3.9235                  0.0611   
1    ...      0.6017      0.3932                  0.1830   
2    ...      2.5003      0.7142                  0.0639   
3    ...      7.6482     12.7188                  0.0831   
4    ...      2.1871     -5.7794                  0.0800   
..   ...         ...         ...                     ...   
791  ...      2.0540     -0.2994                  0.1833   
792  ...      4.7691      2.3442                  0.2202   
793  ...      9.9822      8.1691                  0.1202   
794  ...     -0.3816     -1.0761                  0.1809   
795  ...     20.2469     36.1206                  0.0946   

     spend_breakfastbrunch_ta  spend_dinner_ta  spend_foodbev_ta  \
0                   7069439.0       40790484.0       230383651.0   
1                   4724526.0       25460067.0       160135521.0   
2                   4501211.0       24794631.0       151609187.0   
3                   4038906.0       23214366.0       146417939.0   
4                   5919218.0       32751951.0       207616741.0   
..                        ...              ...               ...   
791                 7614977.0       40037412.0       264008408.0   
792                 5118356.0       28458285.0       197532602.0   
793                 4677280.0       25445615.0       161088758.0   
794                10318478.0       54577513.0       349542567.0   
795                 1973844.0       11925184.0        64941408.0   

     spend_lunch_ta  wealth_hhavg_ta  wealth_hhtotal_ta  white_p_ta  
0        23166216.0         240573.0            25223.0      0.4897  
1        14653701.0   

In [63]:
train_df, test_df = train_test_split(smoothie_merged, test_size=0.1, random_state=42)
X_train = train_df.drop(columns=["category"])
y_train = train_df["category"]
X_test = test_df.drop(columns=["category"])
y_test = test_df["category"]

In [64]:
drop_features = ['store',
 'longitude',
 'latitude',
 'cbsa_name',
 'dma_name',
 'state_name',
 ]

ordinal_features_oth = [
    "market_size",
    "store_density",
]
ordering_ordinal_oth = [
    ["Very Large Metro (1)", "Large Metro (2)", "Large City (3)", "Medium City (4)", "Small City (5)", "Small Town (6)"],
    ["Rural", "Exurban", "Suburban", "Light Suburban", "Light Urban", "Urban", "Super Urban"],
]
numeric_features = list(set(smoothie_merged.select_dtypes(include=np.number).columns.tolist()) - {"longitude", "latitude"})

In [65]:
numeric_transformer = make_pipeline(
    SimpleImputer(strategy="median"), 
    StandardScaler()
)

ordinal_transformer_oth = make_pipeline(
    SimpleImputer(strategy="most_frequent"),
    OrdinalEncoder(categories=ordering_ordinal_oth),
)

preprocessor = make_column_transformer(
    ("drop", drop_features),
    (numeric_transformer, numeric_features),
    (ordinal_transformer_oth, ordinal_features_oth),
)

In [66]:
preprocessor.fit(X_train)

ColumnTransformer(transformers=[('drop', 'drop',
                                 ['store', 'longitude', 'latitude', 'cbsa_name',
                                  'dma_name', 'state_name']),
                                ('pipeline-1',
                                 Pipeline(steps=[('simpleimputer',
                                                  SimpleImputer(strategy='median')),
                                                 ('standardscaler',
                                                  StandardScaler())]),
                                 ['spend_breakfastbrunch_ta',
                                  'emp_accommodation_foodserv_p_3mi',
                                  'hh_7pers_p_ta', 'hh_type_male_nochild_p_ta',
                                  'hh_1ve...
                                 Pipeline(steps=[('simpleimputer',
                                                  SimpleImputer(strategy='most_frequent')),
                                                 ('ordinalencoder',
                                                  OrdinalEncoder(categories=[['Very '
                                                                              'Large '
                                                                              'Metro '
                                                                              '(1)',
                                                                              'Large '
                                                                              'Metro '
                                                                              '(2)',
                                                                              'Large '
                                                                              'City '
                                                                              '(3)',
                                                                              'Medium '
                                                                              'City '
                                                                              '(4)',
                                                                              'Small '
                                                                              'City '
                                                                              '(5)',
                                                                              'Small '
                                                                              'Town '
                                                                              '(6)'],
                                                                             ['Rural',
                                                                              'Exurban',
                                                                              'Suburban',
                                                                              'Light '
                                                                              'Suburban',
                                                                              'Light '
                                                                              'Urban',
                                                                              'Urban',
                                                                              'Super '
                                                                              'Urban']]))]),
                                 ['market_size', 'store_density'])])

In [67]:
column_names = (
    numeric_features
    + preprocessor.named_transformers_['pipeline-2']['ordinalencoder'].get_feature_names_out().tolist()
)
len(column_names)

920

In [86]:
transformed_X_train = preprocessor.transform(X_train)

In [89]:
transformed_X_train_df = pd.DataFrame(transformed_X_train, columns=column_names)
transformed_X_train_df

spend_breakfastbrunch_ta  emp_accommodation_foodserv_p_3mi  \
0                    3.006608                         -0.578451   
1                    1.082548                         -0.527091   
2                   -0.690315                         -0.116207   
3                    0.045323                         -0.013486   
4                    1.011306                         -0.146167   
..                        ...                               ...   
711                 -0.973485                          0.003634   
712                  0.224869                          0.495839   
713                  0.266487                         -0.069126   
714                 -1.391657                         -0.920854   
715                 -0.701384                         -0.330209   

     hh_7pers_p_ta  hh_type_male_nochild_p_ta  hh_1vehicle_p_5mi  \
0        -0.255387                  -1.411746          -2.293129   
1        -0.993526                  -0.277228           0.427386   
2         1.053132                  -1.075928          -1.771367   
3         0.516304                   0.811909          -1.020539   
4        -0.344859                   0.258264          -1.070029   
..             ...                        ...                ...   
711      -1.317860                  -1.257451           1.277194   
712      -0.937607                   0.212884           0.259121   
713       1.008396                   0.076742          -0.880554   
714      -0.031709                  -0.141086           1.183871   
715      -0.356042                  -0.776416           0.676248   

     age0018_p_1mi  hh_type_1pers_p_10mi  hu_ownerocc_1mi  \
0        -0.445402             -1.025068        -0.285635   
1        -0.169020              0.926991         1.572752   
2        -0.042033             -2.235070         0.105572   
3         0.874261             -0.935003         0.332584   
4        -1.184911             -0.696135        -0.336635   
..             ...                   ...              ...   
711       0.702456              1.056214         1.756228   
712      -1.003146              0.578479        -0.512025   
713       1.616260             -1.959002         0.103706   
714       0.500771              0.453171        -0.129525   
715       0.356355              0.210387        -0.192342   

     military_installations_2mi  medsalcy_3mi  ...  emp_manfacturing_p_3mi  \
0                      -0.12555      0.479451  ...                0.366232   
1                      -0.12555      1.109466  ...               -0.013909   
2                      -0.12555      0.197425  ...               -0.287299   
3                      -0.12555      1.169469  ...                0.353214   
4                      -0.12555      0.302638  ...               -0.594537   
..                          ...           ...  ...                     ...   
711                    -0.12555      0.746686  ...               -0.521633   
712                    -0.12555     -1.196983  ...               -0.607556   
713                    -0.12555      0.805167  ...               -0.081606   
714                    -0.12555     -0.154384  ...               -1.091846   
715                    -0.12555     -1.774518  ...               -0.914794   

     spend_lunch_3mi  inrix_dinner_ns  dtpop_students_9th_12th_p_1mi  \
0          -0.101906         0.488229                       2.459765   
1           0.699866         1.207545                      -0.411251   
2          -0.132011         1.333107                       0.999073   
3           0.031376        -0.865277                      -0.814200   
4           0.007517        -0.165114                      -0.411251   
..               ...              ...                            ...   
711         0.527092        -0.354165                      -1.116412   
712        -0.385537        -0.902875                      -0.663094   
713        -0.016699        -0.956788                       0.847

In [90]:
import optuna
from optuna.integration import LightGBMPruningCallback

In [101]:
best_booster = None
lgbm = None

In [102]:
def objective(trial, X, y):
    global lgbm
    param_grid = {
        #         "device_type": trial.suggest_categorical("device_type", ['gpu']),
        "n_estimators": trial.suggest_categorical("n_estimators", [200]),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3),
        "num_leaves": trial.suggest_int("num_leaves", 20, 400, step=20),
        "max_depth": trial.suggest_int("max_depth", 3, 12),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 200, 500, step=100),
        "max_bin": trial.suggest_int("max_bin", 200, 300),
        "lambda_l1": trial.suggest_int("lambda_l1", 0, 100, step=5),
        "lambda_l2": trial.suggest_int("lambda_l2", 0, 100, step=5),
        "min_gain_to_split": trial.suggest_float("min_gain_to_split", 0, 15),
        "bagging_fraction": trial.suggest_float(
            "bagging_fraction", 0.2, 0.95, step=0.1
        ),
        "bagging_freq": trial.suggest_categorical("bagging_freq", [1]),
        "feature_fraction": trial.suggest_float(
            "feature_fraction", 0.2, 0.95, step=0.1
        ),
    }
    
    cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=24)

    cv_scores = np.empty(5)
    for idx, (train_idx, test_idx) in enumerate(cv.split(X, y)):
        # print(idx)
        # print(train_idx)
        # print(test_idx)
        X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
        # print('X_train shape: ', X_train.shape)
        # print('X_test shape: ', X_test.shape)
        y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
        # print('y_train shape: ', y_train.shape)
        # print('y_test shape: ', y_test.shape)

        lgbm = LGBMClassifier(objective="multiclass", **param_grid)
        lgbm.fit(
            X_train,
            y_train,
            eval_set=[(X_test, y_test)],
            eval_metric="multi_logloss",
            early_stopping_rounds=100,
            callbacks=[
                LightGBMPruningCallback(trial, "multi_logloss")
            ],  # Add a pruning callback
        )
        preds = lgbm.predict_proba(X_test)
        cv_scores[idx] = log_loss(y_test, preds)

    return np.mean(cv_scores)

In [103]:
def callback(study, trial):
    global best_booster
    if study.best_trial == trial:
        best_booster = lgbm

In [104]:
study = optuna.create_study(direction="minimize", study_name="LGBM Classifier")
func = lambda trial: objective(trial, transformed_X_train_df, y_train)
study.optimize(func, n_trials=100, callbacks=[callback])

[I 2023-05-17 00:06:41,138] A new study created in memory with name: LGBM Classifier
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/distributions.py:701: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced by [0.2, 0.9].
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.


[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] lambda_l2 is set=50, reg_lambda=0.0 will be ignored. Current value: lambda_l2=50
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7
[LightGBM] [Warning] min_gain_to_split is set=0.05629586349575666, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.05629586349575666
[LightGBM] [Warning] lambda_l1 is set=80, reg_alpha=0.0 will be ignored. Current value: lambda_l1=80
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_

/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 18 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 19 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 20 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 21 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 22 is already reported.
  warnings.warn(
/Users/clin404/minic

[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] lambda_l2 is set=50, reg_lambda=0.0 will be ignored. Current value: lambda_l2=50
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7
[LightGBM] [Warning] min_gain_to_split is set=0.05629586349575666, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.05629586349575666
[LightGBM] [Warning] lambda_l1 is set=80, reg_alpha=0.0 will be ignored. Current value: lambda_l1=80
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] min_data_in_leaf is set=200, min_child_

/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/en

...

[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] min_data_in_leaf is set=200, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=200
[LightGBM] [Warning] lambda_l2 is set=30, reg_lambda=0.0 will be ignored. Current value: lambda_l2=30
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9
[LightGBM] [Warning] min_gain_to_split is set=3.072654914209787, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=3.072654914209787
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0


/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 7 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 8 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 9 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 10 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 11 is already reported.
  warnings.warn(
/Users/clin404/minicond

[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] min_data_in_leaf is set=200, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=200
[LightGBM] [Warning] lambda_l2 is set=30, reg_lambda=0.0 will be ignored. Current value: lambda_l2=30
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9
[LightGBM] [Warning] min_gain_to_split is set=3.072654914209787, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=3.072654914209787
[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0


/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 20 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 21 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 22 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 23 is already reported.
  warnings.warn(
/Users/clin404/miniconda3/envs/575/lib/python3.10/site-packages/optuna/trial/_trial.py:490: UserWarning: The reported value is ignored because this `step` 24 is already reported.
  warnings.warn(
/Users/clin404/minic

[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] min_data_in_leaf is set=200, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=200
[LightGBM] [Warning] lambda_l2 is set=30, reg_lambda=0.0 will be ignored. Current value: lambda_l2=30
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9
[LightGBM] [Warning] min_gain_to_split is set=2.912042216427834, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=2.912042216427834
[LightGBM] [Warning] lambda_l1 is set=10, reg_alpha=0.0 will be ignored. Current value: lambda_l1=10


In [106]:
print(f"\tBest value (multi_logloss): {study.best_value:.5f}")
print(f"\tBest params:")

for key, value in study.best_params.items():
    print(f"\t\t{key}: {value}")

	Best value (multi_logloss): 1.24940
	Best params:
		n_estimators: 200
		learning_rate: 0.2642970892641992
		num_leaves: 180
		max_depth: 11
		min_data_in_leaf: 200
		max_bin: 265
		lambda_l1: 0
		lambda_l2: 15
		min_gain_to_split: 1.9436790687521488
		bagging_fraction: 0.9
		bagging_freq: 1
		feature_fraction: 0.9


In [110]:
best_booster

LGBMClassifier(bagging_fraction=0.9, bagging_freq=1, feature_fraction=0.9,
               lambda_l1=0, lambda_l2=15, learning_rate=0.2642970892641992,
               max_bin=265, max_depth=11, min_data_in_leaf=200,
               min_gain_to_split=1.9436790687521488, n_estimators=200,
               num_leaves=180, objective='multiclass')

In [ ]:
def evaluate_models(X_train, y_train,
		            X_test, y_test,
		    		rfe_estimator, 
		    		rfe_num_features_start,  rfe_num_features_end, rfe_num_features_step, 
				    pipe_model,
					random_state=42):
	
	for i in range(rfe_num_features_start, rfe_num_features_end+1, rfe_num_features_step):
		rfe = RFE(estimator=rfe_estimator, n_features_to_select=i)
		pipe_rfe_model = make_pipeline(preprocessor, 
			                           rfe, 
				                       pipe_model)
		
		pipe_rfe_model.fit(X_train, y_train)
		
		print('---- RFE with ', i, ' features selected ----')
		print(pipe_rfe_model.score(X_train, y_train))
		print(pipe_rfe_model.score(X_test, y_test))	